# Deep Q-Learning 

For this assignment we will implement the Deep Q-Learning algorithm with Experience Replay as described in breakthrough paper __"Playing Atari with Deep Reinforcement Learning"__. We will train an agent to play the famous game of __Breakout__.

In [1]:
import sys
import gym
import torch
import pylab
import random
import numpy as np
import time
from collections import deque
from datetime import datetime
from copy import deepcopy
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
from torch.autograd import Variable
from utils import *
from agent import *
from model import *
from config import *
from env import GameEnv
%matplotlib inline
%load_ext autoreload
%autoreload 2

## Understanding the environment

In the following cell, we initialise our game of __Breakout__ and you can see how the environment looks like. For further documentation of the of the environment refer to https://gym.openai.com/envs. 

In [2]:
envs = []
for i in range(num_envs):
    envs.append(GameEnv('SpaceInvadersDeterministic-v4'))
#env.render()

/usr/local/lib/python3.5/dist-packages/skimage/transform/_warps.py:110: UserWarning: Anti-aliasing will be enabled by default in skimage 0.15 to avoid aliasing artifacts when down-sampling images.
  warn("Anti-aliasing will be enabled by default in skimage 0.15 to "


In [3]:
number_lives = envs[0].life
state_size = envs[0].observation_space.shape
action_size = envs[0].action_space.n
rewards, episodes = [], []

## Creating a DQN Agent

Here we create a DQN Agent. This agent is defined in the __agent.py__. The corresponding neural network is defined in the __model.py__. 

__Evaluation Reward__ : The average reward received in the past 100 episodes/games.

__Frame__ : Number of frames processed in total.

__Memory Size__ : The current size of the replay memory.

In [4]:
agent = Agent(action_size)
torch.save(agent.policy_net.state_dict(), "./save_model/spaceinvaders_ppo_best")
evaluation_reward = deque(maxlen=evaluation_reward_length)
frame = 0
memory_size = 0
reset_max = 10

### Main Training Loop

In [2]:
vis_env_idx = 0
vis_env = envs[vis_env_idx]
e = 0
frame = 0
max_eval = -np.inf
reset_count = 0

while (frame < 10000000):
    step = 0
    assert(num_envs * env_mem_size == train_frame)
    frame_next_vals = []
    for i in range(num_envs):
        env = envs[i]
        #history = env.history
        #life = env.life
        #state, reward, done, info = [env.state, env.reward, env.done, env.info]
        for j in range(env_mem_size):
            step += 1
            frame += 1
            
            curr_state = env.history[HISTORY_SIZE-1,:,:]
            action, value = agent.get_action(np.float32(env.history[:HISTORY_SIZE,:,:]) / 255.)
            
            next_state, env.reward, env.done, env.info = env.step(action)
            
            if (i == vis_env_idx):
                vis_env._env.render()
            
            frame_next_state = get_frame(next_state)
            env.history[HISTORY_SIZE,:,:] = frame_next_state
            terminal_state = check_live(env.life, env.info['ale.lives'])
            
            env.life = env.info['ale.lives']
            r = env.reward
            
            agent.memory.push(i, deepcopy(curr_state), action, r, terminal_state, value, 0, 0)
            if (j == env_mem_size-1):
                _, frame_next_val = agent.get_action(np.float32(env.history[1:,:,:]) / 255.)
                frame_next_vals.append(frame_next_val)
            env.score += r
            env.history[:HISTORY_SIZE, :, :] = env.history[1:,:,:]
            
            if (env.done):
                if (e % 50 == 0):
                    print('now time : ', datetime.now())
                    rewards.append(np.mean(evaluation_reward))
                    episodes.append(e)
                    pylab.plot(episodes, rewards, 'b')
                    pylab.savefig("./save_graph/spaceinvaders_ppo.png")
                    torch.save(agent.policy_net, "./save_model/spaceinvaders_ppo")
                    
                    if np.mean(evaluation_reward) > max_eval:
                        torch.save(agent.policy_net.state_dict(), "./save_model/spaceinvaders_ppo_best")
                        max_eval = float(np.mean(evaluation_reward))
                        reset_count = 0
                    elif e > 5000:
                        reset_count += 1
                        """
                        if (reset_count == reset_max):
                            print("Training went nowhere, starting again at best model")
                            agent.policy_net.load_state_dict(torch.load("./save_model/spaceinvaders_ppo_best"))
                            agent.update_target_net()
                            reset_count = 0
                        """
                e += 1
                evaluation_reward.append(env.score)
                print("episode:", e, "  score:", env.score,  " epsilon:", agent.epsilon, "   steps:", step,
                  " evaluation reward:", np.mean(evaluation_reward))
                
                env.done = False
                env.score = 0
                env.history = np.zeros([HISTORY_SIZE+1,84,84], dtype=np.uint8)
                env.state = env.reset()
                env.life = number_lives
                get_init_state(env.history, env.state)
                
                
                
    agent.train_policy_net(frame, frame_next_vals)
    agent.update_target_net()


NameError: name 'envs' is not defined

In [ ]:
torch.save(agent.policy_net, "./save_model/spaceinvaders_ppo")

In [ ]:
### Loop through all environments and run PPO on them

env_names = ['SpaceInvaders-v0', 'MsPacman-v0', 'Asteroids-v0', 'Asterix-v0', 'Atlantis-v0', 'Alien-v0', 'Amidar-v0', 'Assault-v0', 'BankHeist-v0']

for a in range(len(env_names)):
    name = env_names[a]
    print("\n\n\n ------- STARTING TRAINING FOR %s ------- \n\n\n" % (name))
    
    envs = []
    for i in range(num_envs):
        envs.append(GameEnv(name))
    #env.render()
    

    number_lives = envs[0].life
    state_size = envs[0].observation_space.shape
    if (name == 'SpaceInvaders-v0'):
        action_size = 4
    else:
        action_size = envs[0].action_space.n
    rewards, episodes = [], []

    vis_env_idx = 0
    vis_env = envs[vis_env_idx]
    e = 0
    frame = 0
    max_eval = -np.inf
    reset_count = 0


    agent = Agent(action_size)
    torch.save(agent.policy_net.state_dict(), "./save_model/" + name + "_best")
    evaluation_reward = deque(maxlen=evaluation_reward_length)
    frame = 0
    memory_size = 0
    reset_max = 10
    
    print("Determing min/max rewards of environment")
    [low, high] = score_range = get_score_range(name)
    print("Min: %d. Max: %d." % (low, high))

    while (frame < 10000000):
        step = 0
        assert(num_envs * env_mem_size == train_frame)
        frame_next_vals = []
        
        for j in range(env_mem_size):
            
            curr_states = np.stack([envs[i].history[HISTORY_SIZE-1,:,:] for i in range(num_envs)])
            next_states = []
            net_in = np.stack([envs[i].history[:HISTORY_SIZE,:,:] for i in range(num_envs)])
            step += num_envs
            frame += num_envs
            actions, values = agent.get_action(np.float32(net_in) / 255.)
            
            for i in range(num_envs):
                env = envs[i]
                next_state, env.reward, env.done, env.info = env.step(actions[i])
                next_states.append(next_state)
                if (i == vis_env_idx):
                    vis_env._env.render()
            
            for i in range(num_envs):
                env = envs[i]
                """
                next_state, env.reward, env.done, env.info = env.step(actions[i])
                if (i == vis_env_idx):
                    vis_env._env.render()
                """
                
                frame_next_state = get_frame(next_states[i])
                env.history[HISTORY_SIZE,:,:] = frame_next_state
                terminal_state = check_live(env.life, env.info['ale.lives'])
                env.life = env.info['ale.lives']
                r = (env.reward / high) * 20.0 #np.log(max(env.reward+1, 1))#((env.reward - low) / (high - low)) * 30
                agent.memory.push(i, deepcopy(curr_states[i]), actions[i], r, terminal_state, values[i], 0, 0)
                
                if (j == env_mem_size-1):
                    net_in = np.stack([envs[k].history[1:,:,:] for k in range(num_envs)])
                    _, frame_next_vals = agent.get_action(np.float32(net_in) / 255.)
                
                env.score += env.reward
                env.history[:HISTORY_SIZE, :, :] = env.history[1:,:,:]
        
                if (env.done):
                    if (e % 50 == 0):
                        print('now time : ', datetime.now())
                        rewards.append(np.mean(evaluation_reward))
                        episodes.append(e)
                        pylab.plot(episodes, rewards, 'b')
                        pylab.savefig("./save_graph/" + name + "_ppo.png")
                        torch.save(agent.policy_net, "./save_model/" + name + "_ppo")

                        if np.mean(evaluation_reward) > max_eval:
                            torch.save(agent.policy_net.state_dict(), "./save_model/"  + name + "_ppo_best")
                            max_eval = float(np.mean(evaluation_reward))
                            reset_count = 0
                        elif e > 5000:
                            reset_count += 1
                            """
                            if (reset_count == reset_max):
                                print("Training went nowhere, starting again at best model")
                                agent.policy_net.load_state_dict(torch.load("./save_model/spaceinvaders_ppo_best"))
                                agent.update_target_net()
                                reset_count = 0
                            """
                    e += 1
                    evaluation_reward.append(env.score)
                    print("episode:", e, "  score:", env.score,  " epsilon:", agent.epsilon, "   steps:", step,
                      " evaluation reward:", np.mean(evaluation_reward))

                    env.done = False
                    env.score = 0
                    env.history = np.zeros([HISTORY_SIZE+1,84,84], dtype=np.uint8)
                    env.state = env.reset()
                    env.life = number_lives
                    get_init_state(env.history, env.state)
            
        agent.train_policy_net(frame, frame_next_vals)
        agent.update_target_net()
    print("FINISHED TRAINING FOR %s" % (name))
    pylab.figure()




 ------- STARTING TRAINING FOR SpaceInvaders-v0 ------- 





/home/sigai/anaconda3/envs/py36/lib/python3.6/site-packages/skimage/transform/_warps.py:110: UserWarning: Anti-aliasing will be enabled by default in skimage 0.15 to avoid aliasing artifacts when down-sampling images.
  warn("Anti-aliasing will be enabled by default in skimage 0.15 to "


Determing min/max rewards of environment
Min: 0. Max: 200.


/home/sigai/Documents/Projects/Object-Recognition/assignment5_materials/Assignment5_PPO/Assignment5/model.py:45: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  probs = F.softmax(x[:,:self.action_size] - torch.max(x[:,:self.action_size],1)[0].unsqueeze(1))


Training network. lr: 0.000250. clip: 0.100000


...

Training network. lr: 0.000197. clip: 0.078960
Iteration 6874: Policy loss: 0.010001. Value loss: 0.636243. Entropy: 1.828645.
Iteration 6875: Policy loss: -0.004295. Value loss: 0.376430. Entropy: 1.828899.
Iteration 6876: Policy loss: -0.008931. Value loss: 0.281386. Entropy: 1.824000.
Training network. lr: 0.000197. clip: 0.078960
Iteration 6877: Policy loss: 0.007448. Value loss: 1.047811. Entropy: 1.952200.
Iteration 6878: Policy loss: -0.007577. Value loss: 0.698802. Entropy: 1.954474.
Iteration 6879: Policy loss: -0.014666. Value loss: 0.527225. Entropy: 1.959084.
Training network. lr: 0.000197. clip: 0.078960
Iteration 6880: Policy loss: 0.002383. Value loss: 0.842471. Entropy: 1.918407.
Iteration 6881: Policy loss: -0.006069. Value loss: 0.518085. Entropy: 1.923140.
Iteration 6882: Policy loss: -0.014510. Value loss: 0.372356. Entropy: 1.903640.
episode: 2250   score: 830.0  epsilon: 1.0    steps: 832  evaluation reward: 1039.1
now time :  2019-03-06 11:13:38.303827
episode: 2

Iteration 6942: Policy loss: -0.013798. Value loss: 0.439070. Entropy: 1.777806.
Training network. lr: 0.000197. clip: 0.078812
Iteration 6943: Policy loss: 0.010377. Value loss: 0.641862. Entropy: 1.666797.
Iteration 6944: Policy loss: -0.006969. Value loss: 0.423632. Entropy: 1.686804.
Iteration 6945: Policy loss: -0.016180. Value loss: 0.340444. Entropy: 1.661907.
episode: 2269   score: 1180.0  epsilon: 1.0    steps: 992  evaluation reward: 1101.0
Training network. lr: 0.000197. clip: 0.078812
Iteration 6946: Policy loss: 0.011389. Value loss: 0.703044. Entropy: 1.630524.
Iteration 6947: Policy loss: -0.005700. Value loss: 0.433706. Entropy: 1.607209.
Iteration 6948: Policy loss: -0.011085. Value loss: 0.318321. Entropy: 1.605069.
Training network. lr: 0.000197. clip: 0.078812
Iteration 6949: Policy loss: 0.010329. Value loss: 0.823826. Entropy: 1.543516.
Iteration 6950: Policy loss: 0.000494. Value loss: 0.519084. Entropy: 1.541974.
Iteration 6951: Policy loss: -0.010700. Value los

Iteration 7010: Policy loss: -0.002509. Value loss: 0.444585. Entropy: 1.534002.
Iteration 7011: Policy loss: -0.015448. Value loss: 0.337692. Entropy: 1.522084.
Training network. lr: 0.000196. clip: 0.078499
Iteration 7012: Policy loss: 0.005226. Value loss: 0.730878. Entropy: 1.740042.
Iteration 7013: Policy loss: -0.007713. Value loss: 0.412880. Entropy: 1.745374.
Iteration 7014: Policy loss: -0.012654. Value loss: 0.269414. Entropy: 1.718753.
Training network. lr: 0.000196. clip: 0.078499
Iteration 7015: Policy loss: 0.008263. Value loss: 0.728185. Entropy: 1.807267.
Iteration 7016: Policy loss: -0.008171. Value loss: 0.440993. Entropy: 1.819609.
Iteration 7017: Policy loss: -0.016770. Value loss: 0.259039. Entropy: 1.794860.
Training network. lr: 0.000196. clip: 0.078499
Iteration 7018: Policy loss: 0.016617. Value loss: 1.110807. Entropy: 1.867421.
Iteration 7019: Policy loss: -0.002519. Value loss: 0.681738. Entropy: 1.850068.
Iteration 7020: Policy loss: -0.010188. Value loss: 

Iteration 7079: Policy loss: -0.004846. Value loss: 0.423706. Entropy: 1.650413.
Iteration 7080: Policy loss: -0.014121. Value loss: 0.327365. Entropy: 1.657966.
Training network. lr: 0.000196. clip: 0.078352
Iteration 7081: Policy loss: 0.008209. Value loss: 1.007570. Entropy: 1.668484.
Iteration 7082: Policy loss: -0.007463. Value loss: 0.624113. Entropy: 1.680873.
Iteration 7083: Policy loss: -0.010367. Value loss: 0.496794. Entropy: 1.691687.
Training network. lr: 0.000196. clip: 0.078352
Iteration 7084: Policy loss: 0.008873. Value loss: 1.075544. Entropy: 1.731397.
Iteration 7085: Policy loss: -0.007280. Value loss: 0.768021. Entropy: 1.754236.
Iteration 7086: Policy loss: -0.017394. Value loss: 0.629957. Entropy: 1.722867.
episode: 2307   score: 1180.0  epsilon: 1.0    steps: 520  evaluation reward: 1159.4
Training network. lr: 0.000196. clip: 0.078352
Iteration 7087: Policy loss: 0.002198. Value loss: 1.414263. Entropy: 1.750092.
Iteration 7088: Policy loss: 0.003898. Value los

Iteration 7149: Policy loss: -0.011190. Value loss: 0.231563. Entropy: 1.673953.
episode: 2325   score: 160.0  epsilon: 1.0    steps: 832  evaluation reward: 1211.8
Training network. lr: 0.000195. clip: 0.078195
Iteration 7150: Policy loss: 0.012630. Value loss: 0.745687. Entropy: 1.690140.
Iteration 7151: Policy loss: -0.001322. Value loss: 0.415186. Entropy: 1.707564.
Iteration 7152: Policy loss: -0.011297. Value loss: 0.310669. Entropy: 1.691629.
episode: 2326   score: 1300.0  epsilon: 1.0    steps: 544  evaluation reward: 1217.0
episode: 2327   score: 1080.0  epsilon: 1.0    steps: 824  evaluation reward: 1216.0
Training network. lr: 0.000195. clip: 0.078038
Iteration 7153: Policy loss: 0.003249. Value loss: 0.952412. Entropy: 1.786503.
Iteration 7154: Policy loss: -0.009981. Value loss: 0.638099. Entropy: 1.808880.
Iteration 7155: Policy loss: -0.019445. Value loss: 0.497665. Entropy: 1.793057.
episode: 2328   score: 780.0  epsilon: 1.0    steps: 672  evaluation reward: 1211.0
Tra